In [1]:
import numpy as np
import matplotlib.pyplot as plt
import pandas as pd
import scanpy as sc
import scipy.io as sio
import anndata as ad
import seaborn as sns
import os as os
import sys as sys
sys.path.append('/home/qiuaodon/Desktop/PanCancer_scRNA_analysis/utils/')
from scRNA_utils import *
import operator as op
import matplotlib.colors as mcolors
data_dir_NHDP = "/home/qiuaodon/Desktop/project_data_new/"
data_dir = "/home/qiuaodon/Desktop/PanCancer_scRNA_analysis/CD4_CD8_final_version/"

## check the patients I can use with enough cells in subtypes


In [2]:
adata_T = sc.read(data_dir_NHDP + '1863-counts_cells_cohort1_T_cells_annotated.h5ad')

In [3]:
# get adata_CD4EX and adata_CD8EX
adata_CD4EX = adata_T[adata_T.obs['cell_type'] == 'CD4 EX', :]
adata_CD8EX = adata_T[adata_T.obs['cell_type'] == 'CD8 EX', :]

In [4]:
# check the number of cells for sample_id, find the patient_ids with more than 5 cells in both pre and on timepoints
cell_counts = adata_CD4EX.obs.groupby(['patient_id', 'timepoint'])['sample_id'].count().unstack()

# Filter patients with more than 5 cells in both 'pre' and 'on' timepoints
valid_patients_CD4EX = cell_counts[(cell_counts['pre'] > 5) & (cell_counts['on'] > 5)].index.tolist()
valid_patients_CD4EX = set(valid_patients_CD4EX)
# check the number of cells for sample_id, find the patient_ids with more than 5 cells in both pre and on timepoints in CD8EX
cell_counts = adata_CD8EX.obs.groupby(['patient_id', 'timepoint'])['sample_id'].count().unstack()

# Filter patients with more than 5 cells in both 'pre' and 'on' timepoints
valid_patients_CD8EX = cell_counts[(cell_counts['pre'] > 5) & (cell_counts['on'] > 5)].index.tolist()
valid_patients_CD8EX = set(valid_patients_CD8EX)

/tmp/ipykernel_3304168/2168074212.py:2: FutureWarning: The default of observed=False is deprecated and will be changed to True in a future version of pandas. Pass observed=False to retain current behavior or observed=True to adopt the future default and silence this warning.
  cell_counts = adata_CD4EX.obs.groupby(['patient_id', 'timepoint'])['sample_id'].count().unstack()
/tmp/ipykernel_3304168/2168074212.py:8: FutureWarning: The default of observed=False is deprecated and will be changed to True in a future version of pandas. Pass observed=False to retain current behavior or observed=True to adopt the future default and silence this warning.
  cell_counts = adata_CD8EX.obs.groupby(['patient_id', 'timepoint'])['sample_id'].count().unstack()


In [ ]:
adata_Fibro = sc.read(data_dir_NHDP + '1863-counts_cells_cohort1_Fibro_cells.h5ad')

In [ ]:
# check the number of cells for sample_id, find the patient_ids with more than 5 cells in both pre and on timepoints
cell_counts = adata_Fibro.obs.groupby(['patient_id', 'timepoint'])['sample_id'].count().unstack()

# Filter patients with more than 5 cells in both 'pre' and 'on' timepoints
valid_patients_Fibro = cell_counts[(cell_counts['pre'] > 5) & (cell_counts['on'] > 5)].index.tolist()
valid_patients_Fibro = set(valid_patients_Fibro)

/tmp/ipykernel_3304168/292830472.py:2: FutureWarning: The default of observed=False is deprecated and will be changed to True in a future version of pandas. Pass observed=False to retain current behavior or observed=True to adopt the future default and silence this warning.
  cell_counts = adata_M1.obs.groupby(['patient_id', 'timepoint'])['sample_id'].count().unstack()


# get the DEGs of filtered patients of CD8EX and Mono

In [ ]:
Patients_CD8EX_Fibro = list(valid_patients_CD8EX & valid_patients_Fibro)
adata_CD8EX_1 = adata_CD8EX[adata_CD8EX.obs['patient_id'].isin(Patients_CD8EX_Fibro), :]
adata_Fibro_1 = adata_Fibro[adata_Fibro.obs['patient_id'].isin(Patients_CD8EX_Fibro), :]

In [12]:
DEG_1 = paird_ttest(adata_CD8EX_1, condition_key = 'timepoint', sample_id_col = 'sample_id', patient_id_col = 'patient_id')
DEG_1 = DEG_1[DEG_1['pval'] < 0.01]

Input adata is not pseudo-bulk RNA data. Convert to pseudo-bulk RNA data.


/home/qiuaodon/Desktop/PanCancer_scRNA_analysis/utils/scRNA_utils.py:490: FutureWarning: Downcasting behavior in `replace` is deprecated and will be removed in a future version. To retain the old behavior, explicitly call `result.infer_objects(copy=False)`. To opt-in to the future behavior, set `pd.set_option('future.no_silent_downcasting', True)`
  res_df['pval'] = res_df['pval'].replace([np.inf, -np.inf], np.nan)  # Replace infinite values with NaN


In [13]:
# remove the DEGs with . in the gene names
DEG_1 = DEG_1[~DEG_1.index.str.contains('\.')]

In [ ]:
DEG_2 = paird_ttest(adata_Fibro_1, condition_key = 'timepoint', sample_id_col = 'sample_id', patient_id_col = 'patient_id')
DEG_2 = DEG_2[DEG_2['pval'] < 0.01]

Input adata is not pseudo-bulk RNA data. Convert to pseudo-bulk RNA data.


/home/qiuaodon/Desktop/PanCancer_scRNA_analysis/utils/scRNA_utils.py:490: FutureWarning: Downcasting behavior in `replace` is deprecated and will be removed in a future version. To retain the old behavior, explicitly call `result.infer_objects(copy=False)`. To opt-in to the future behavior, set `pd.set_option('future.no_silent_downcasting', True)`
  res_df['pval'] = res_df['pval'].replace([np.inf, -np.inf], np.nan)  # Replace infinite values with NaN


In [15]:
DEG_2 = DEG_2[~DEG_2.index.str.contains('\.')]

## IVA

In [ ]:
adata_1_pseudo = scRNA2PseudoBulkAnnData(adata_CD8EX_1, sample_id_col='sample_id')
adata_2_pseudo = scRNA2PseudoBulkAnnData(adata_Fibro_1, sample_id_col='sample_id')

In [ ]:
gene_1 = DEG_1.index.tolist()
gene_2 = DEG_2.index.tolist()

# Filter out invalid gene names
gene_1 = [gene for gene in gene_1 if gene in adata_1_pseudo.var_names]
gene_2 = [gene for gene in gene_2 if gene in adata_2_pseudo.var_names]

gene_1_matrix = adata_1_pseudo[:, gene_1].X
gene_2_matrix = adata_2_pseudo[:, gene_2].X
gene_1_df = pd.DataFrame(gene_1_matrix, columns=gene_1, index=adata_1_pseudo.obs['sample_id'])
gene_2_df = pd.DataFrame(gene_2_matrix, columns=gene_2, index=adata_2_pseudo.obs['sample_id'])
gene_1_df.columns = [i + '_T' for i in gene_1_df.columns]
gene_2_df.columns = [i + '_Fibro' for i in gene_2_df.columns]
gene_df = gene_1_df
gene_df = pd.merge(gene_df, gene_2_df, on='sample_id')
gene_df['treatment'] = gene_df.index.str.contains('On').astype(int)
# get patient id from sample id remove the _On or _Pre
gene_df['patient_id'] = gene_df.index.str.replace('_On', '').str.replace('_Pre', '')

In [20]:
# export the gene_df to csv
gene_df.to_csv(data_dir + 'gene_df_CD8EX_Fibro.csv')

## load in IV result and perform CIT

In [21]:
DEG_pairs = pd.read_excel(data_dir + 'IV_regression_results_with_FisherZ_CD8EX_Fibro.xlsx')

In [22]:
DEG_pairs = DEG_pairs.rename(columns = {'gene_T':'g1', 'gene_cell':'g2'})
calculate_gene_correlation(DEG_pairs, adata_1_pseudo, adata_2_pseudo)

/home/qiuaodon/Desktop/PanCancer_scRNA_analysis/utils/scRNA_utils.py:914: FutureWarning: Setting an item of incompatible dtype is deprecated and will raise an error in a future version of pandas. Value '0.39321307501765923' has dtype incompatible with int64, please explicitly cast to a compatible dtype first.
  results.loc[index, 'g1vsg2_correlation'] = corr_g1_g2


g1             g2  p_value_iv  r_squared_iv  p_value_ci  \
0     ANKRD28_T     ABL2_Fibro    0.024516     -0.083283    0.055801   
1     ANKRD28_T  ADAMTS5_Fibro    0.054148     -0.458176    0.005015   
2     ANKRD28_T  ARHGEF7_Fibro    0.070349     -0.332820    0.020790   
3     ANKRD28_T     ATF3_Fibro    0.009256     -0.348469    0.000908   
4     ANKRD28_T     BTG1_Fibro    0.071526     -0.232574    0.048872   
...         ...            ...         ...           ...         ...   
3343  ZFP36L2_T   TRIM66_Fibro    0.059488     -0.477700    0.029582   
3344  ZFP36L2_T    TRPV1_Fibro    0.086123     -0.377844    0.063985   
3345  ZFP36L2_T  TSC22D3_Fibro    0.006577     -0.731206    0.000009   
3346  ZFP36L2_T     WARS_Fibro    0.088387     -0.635225    0.018758   
3347  ZFP36L2_T     YOD1_Fibro    0.058257     -0.846496    0.004076   

      q_value_iv  q_value_ci  g1vsg2_correlation  
0       0.085916    0.083889            0.393213  
1       0.100103    0.020252           -0.160990  
2       0.109236    0.043997            0.172259  
3       0.077281    0.007544            0.414417  
4       0.109780    0.076281            0.217905  
...          ...         ...                 ...  
3343    0.103976    0.054930           -0.269184  
3344    0.120242    0.092625            0.233514  
3345    0.072295    0.000528            0.584729  
3346    0.122179    0.041399            0.146351  
3347    0.102787    0.018167           -0.189589  

[3348 rows x 8 columns]

In [23]:
# Combine the two conditions using the logical OR operator
DEG_pairs = DEG_pairs[(DEG_pairs['g1vsg2_correlation'] > 0.4) | (DEG_pairs['g1vsg2_correlation'] < -0.4)]
DEG_pairs = DEG_pairs[(DEG_pairs['p_value_ci'] > 0.1)]
# sort the DEG_pairs by g1vsg2_correlation
DEG_pairs = DEG_pairs.sort_values(by='g1vsg2_correlation', ascending=False)
DEG_pairs

g1             g2  p_value_iv  r_squared_iv  p_value_ci  \
488      CBLB_T     SGK1_Fibro    0.003773      0.622287    0.873428   
938     DUSP1_T    CEBPD_Fibro    0.000188      0.564762    0.184103   
1696    IL6ST_T    FKBP5_Fibro    0.000376      0.563744    0.445880   
895    DNAJB1_T   HSPA1A_Fibro    0.001033      0.502519    0.280217   
1052     ERN1_T     WARS_Fibro    0.003245      0.530272    0.585479   
...         ...            ...         ...           ...         ...   
125    ARID5B_T  ADAMTS5_Fibro    0.004507      0.403588    0.605025   
1076    FASLG_T    FKBP5_Fibro    0.000959      0.468799    0.526854   
1614    IER5L_T  ARHGEF7_Fibro    0.007272      0.454370    0.376225   
3239  ZFP36L1_T  DENND6B_Fibro    0.001949      0.521134    0.987509   
2559     SAT1_T    DLEU2_Fibro    0.002062      0.610370    0.594382   

      q_value_iv  q_value_ci  g1vsg2_correlation  
488     0.064760    0.877622            0.800976  
938     0.037183    0.211232            0.794192  
1696    0.045800    0.461740            0.773366  
895     0.051800    0.304008            0.754971  
1052    0.063681    0.597435            0.752816  
...          ...         ...                 ...  
125     0.067365    0.615691           -0.662944  
1076    0.051800    0.539916           -0.707884  
1614    0.072295    0.394983           -0.734891  
3239    0.058678    0.988395           -0.737524  
2559    0.058678    0.605965           -0.802092  

[494 rows x 8 columns]

In [24]:
lrpair = pd.read_csv('/home/qiuaodon/Desktop/project_data_new/lr_network_unique.tsv', sep='\t')

In [25]:
# remove the ppi_prediction and ppi_prediction_go
lrpair = lrpair[lrpair['database'] != 'ppi_prediction']
lrpair = lrpair[lrpair['database'] != 'ppi_prediction_go']
lrpair = lrpair[['from', 'to']]
# change from as L and to as R
lrpair.columns = ['L', 'R']
lrpair

L      R
0      CXCL1  CXCR2
1      CXCL2  CXCR2
2      CXCL3  CXCR2
3      CXCL5  CXCR2
4       PPBP  CXCR2
...      ...    ...
1387  COL2A1   SDC1
1388   LAMA1   SV2A
1389  COL2A1    GP6
1390   LAMA1   DAG1
1391  CCL3L3   CCR1

[1392 rows x 2 columns]

In [26]:
# Check expression in adata_1_pseudo
expressed_genes_1 = adata_1_pseudo.var_names[adata_1_pseudo.X.sum(axis=0) > 0].tolist()

# Check expression in adata_2_pseudo
expressed_genes_2 = adata_2_pseudo.var_names[adata_2_pseudo.X.sum(axis=0) > 0].tolist()

# Filter lrpair where both L and R are expressed in their respective datasets
lrpair = lrpair[
    (lrpair['L'].isin(expressed_genes_1)) & 
    (lrpair['R'].isin(expressed_genes_2))
].reset_index(drop=True)
lrpair

L       R
0    CXCL12   CXCR4
1     CCL17    CCR4
2     CCL22    CCR4
3     CCL19    CCR7
4     CCL21    CCR7
..      ...     ...
154  COL2A1   ITGA1
155  COL2A1   ITGA3
156  COL2A1  ITGA11
157  COL2A1   ITGB8
158  COL2A1    SDC1

[159 rows x 2 columns]

## CIT Fisherz

In [27]:
results = CIT_test(DEG_pairs, lrpair, adata_1_pseudo, adata_2_pseudo, gene_df, method = 'fisherz', p_value_threshold=0.05)

/home/qiuaodon/anaconda3/lib/python3.11/site-packages/numpy/lib/function_base.py:2897: RuntimeWarning: invalid value encountered in divide
  c /= stddev[:, None]
/home/qiuaodon/anaconda3/lib/python3.11/site-packages/numpy/lib/function_base.py:2898: RuntimeWarning: invalid value encountered in divide
  c /= stddev[None, :]
/home/qiuaodon/anaconda3/lib/python3.11/site-packages/numpy/lib/function_base.py:2897: RuntimeWarning: invalid value encountered in divide
  c /= stddev[:, None]
/home/qiuaodon/anaconda3/lib/python3.11/site-packages/numpy/lib/function_base.py:2898: RuntimeWarning: invalid value encountered in divide
  c /= stddev[None, :]
/home/qiuaodon/anaconda3/lib/python3.11/site-packages/numpy/lib/function_base.py:2897: RuntimeWarning: invalid value encountered in divide
  c /= stddev[:, None]
/home/qiuaodon/anaconda3/lib/python3.11/site-packages/numpy/lib/function_base.py:2898: RuntimeWarning: invalid value encountered in divide
  c /= stddev[None, :]
/home/qiuaodon/anaconda3/lib

In [28]:
#calculate the correlation between g1 and g2
calculate_gene_correlation(results, adata_1_pseudo, adata_2_pseudo)
calculate_residuals_correlation(results, adata_1_pseudo, adata_2_pseudo)

/home/qiuaodon/Desktop/PanCancer_scRNA_analysis/utils/scRNA_utils.py:914: FutureWarning: Setting an item of incompatible dtype is deprecated and will raise an error in a future version of pandas. Value '0.5988860864299468' has dtype incompatible with int64, please explicitly cast to a compatible dtype first.
  results.loc[index, 'g1vsg2_correlation'] = corr_g1_g2
/home/qiuaodon/Desktop/PanCancer_scRNA_analysis/utils/scRNA_utils.py:1060: FutureWarning: Setting an item of incompatible dtype is deprecated and will raise an error in a future version of pandas. Value '0.3357765910395746' has dtype incompatible with int64, please explicitly cast to a compatible dtype first.
  results.at[index, 'g1_residualvsg2_residuals_correlation'] = corr


g1            g2       L       R    pValue  g1vsg2_correlation  \
0     ANKRD36B_T  PTGER3_Fibro  COL1A1  ITGA10  0.138324            0.598886   
1        PRDM1_T  ERRFI1_Fibro   ITGAM   ICAM1  0.052962            0.598281   
2       ARID5B_T  IL18BP_Fibro   ITGA4   VCAM1  0.053430            0.588841   
3        AZGP1_T   DLEU2_Fibro     FN1    SDC1  0.056531            0.578070   
4        AZGP1_T   DLEU2_Fibro   THBS1    SDC1  0.079417            0.578070   
...          ...           ...     ...     ...       ...                 ...   
8977   TNFSF14_T  IL18BP_Fibro   ITGA4   VCAM1  0.144862           -0.561755   
8978  ANKRD36B_T   DEPP1_Fibro  COL1A1  ITGA10  0.083226           -0.566072   
8979     IER5L_T    BTG1_Fibro   ICAM1   ITGAX  0.101076           -0.569343   
8980     ZFP36_T  CCDC14_Fibro   LAMC2   ITGA3  0.052952           -0.569952   
8981   ZFP36L2_T   SFRP2_Fibro    IL21   IL2RG  0.077219           -0.594451   

      g1_residualvsg2_residuals_correlation  
0                                  0.335777  
1                                  0.426932  
2                                  0.426199  
3                                  0.421460  
4                                  0.391390  
...                                     ...  
8977                              -0.330719  
8978                              -0.387028  
8979                              -0.368315  
8980                              -0.426948  
8981                              -0.393977  

[8982 rows x 7 columns]

In [37]:
results_filtered = results[(results['pValue'] > 0.1)]
results_filtered = results_filtered[(results_filtered['g1vsg2_correlation'] > 0.4)]
results_filtered = results_filtered[(results_filtered['g1_residualvsg2_residuals_correlation'] < 0.3)]
results_filtered = results_filtered[(results_filtered['g1_residualvsg2_residuals_correlation'] > -0.3)]
results_filtered 

g1               g2         L          R    pValue  \
23    RASGEF1B_T     PTGER3_Fibro    COL1A1     ITGA10  0.224372   
77       CH25H_T       RHOB_Fibro     LAMB1      ITGA6  0.194417   
103       CCNH_T     IL18BP_Fibro     ITGA4      VCAM1  0.209332   
192       IER2_T       ELF3_Fibro       TNF   TNFRSF21  0.344607   
228      AZGP1_T  LINC01355_Fibro       FN1       SDC1  0.284776   
...          ...              ...       ...        ...       ...   
4827     PRDM1_T     NFKBIZ_Fibro     CYR61      ITGA5  0.303566   
4878     SYTL3_T      TRPV1_Fibro  TNFSF13B  TNFRSF13B  0.205972   
4911     SYTL3_T      TRPV1_Fibro    ANGPT1       TIE1  0.251260   
4913     SYTL3_T      TRPV1_Fibro      BMP6     ACVR2B  0.224594   
4914     SYTL3_T      TRPV1_Fibro      BMP7     ACVR2B  0.208209   

      g1vsg2_correlation  g1_residualvsg2_residuals_correlation  
23              0.549589                               0.278794  
77              0.523377                               0.296660  
103             0.513731                               0.287557  
192             0.493944                               0.219150  
228             0.490673                               0.246910  
...                  ...                                    ...  
4827            0.401662                               0.237850  
4878            0.400661                               0.289570  
4911            0.400661                               0.264016  
4913            0.400661                               0.278668  
4914            0.400661                               0.288228  

[88 rows x 7 columns]

In [38]:
results_filtered['L_R'] = results_filtered['L'] + '_' + results_filtered['R']
results_filtered['L_R'].nunique()

36

In [39]:
results_filtered.to_csv(data_dir + 'CIT_test_results_CD8EX_Fibro_results.csv')

In [43]:
import pandas as pd
import numpy as np

# Sample data (assuming results_filtered is already available)
# Adjusting the script to use absolute mean and determine final sign based on majority sign

grouped_results = results_filtered.groupby(["L", "R"])

# Create a new DataFrame to hold the GEM1 and GEM2 groupings
tracked_gem1 = set()
tracked_gem2 = set()

min_gene_num = 2

# Temporary list to hold data before creating DataFrame
temp_data = []

for (ligand, receptor), group in grouped_results:
    gem1 = group["g1"].drop_duplicates().tolist()
    gem2 = group["g2"].drop_duplicates().tolist()
    
    # Calculate mean correlation values using absolute mean
    g1vsg2_corr_mean = np.abs(group["g1vsg2_correlation"]).mean()
    g1_res_vs_g2_res_mean = np.abs(group["g1_residualvsg2_residuals_correlation"]).mean()
    p_value_mean = group["pValue"].mean()
    
    # Determine final sign based on majority sign of correlations
    sign_g1vsg2 = np.sign(group["g1vsg2_correlation"]).sum()
    sign_g1_res_vs_g2_res = np.sign(group["g1_residualvsg2_residuals_correlation"]).sum()
    
    final_g1vsg2_corr = g1vsg2_corr_mean * (1 if sign_g1vsg2 >= 0 else -1)
    final_g1_res_vs_g2_res = g1_res_vs_g2_res_mean * (1 if sign_g1_res_vs_g2_res >= 0 else -1)
    
    # Check the overlap between current GEM_g1 and previously tracked GEM_g1
    overlap_gem1 = len(set(gem1) & tracked_gem1)
    overlap_gem2 = len(set(gem2) & tracked_gem2)
    
    # Filter to include only those with at least three genes in GEM_g1
    if len(gem1) > min_gene_num and len(gem2) > min_gene_num:
        temp_data.append({
            "Ligand": ligand,
            "Receptor": receptor,
            "GEM1_elements": gem1,
            "GEM2_elements": gem2,
            "Num_genes_GEM1": len(gem1),
            "Num_genes_GEM2": len(gem2),
            "GEM1vsGEM2_corr(mean)": final_g1vsg2_corr,
            "GEM1_residualvsGEM2_residual_corr(mean)": final_g1_res_vs_g2_res,
            "average_significance": p_value_mean
        })
        # Update the tracked GEM_g1 and GEM_g2 sets
        tracked_gem1.update(gem1)
        tracked_gem2.update(gem2)

# Convert the temporary data to a DataFrame
grouped_df = pd.DataFrame(temp_data)
# rank each GEM_g1 by order of name inside
grouped_df['GEM1_elements'] = grouped_df['GEM1_elements'].apply(lambda x: sorted(x))
grouped_df['GEM2_elements'] = grouped_df['GEM2_elements'].apply(lambda x: sorted(x))
grouped_df

Ligand  Receptor                                      GEM1_elements  \
0  COL1A1    ITGA10          [DUSP1_T, PRDM1_T, RASGEF1B_T, ZFP36L2_T]   
1   CYR61     ITGA5                [DUSP1_T, PELI1_T, PRDM1_T, SGK1_T]   
2   ITGA4     VCAM1  [ARID5B_T, BCL2L11_T, CCNH_T, CH25H_T, HSPH1_T...   
3   ITGAM     ICAM1                         [IRF8_T, PELI1_T, PRDM1_T]   
4   THBS1      SDC1                        [AZGP1_T, IER5L_T, PRDM1_T]   
5     TNF  TNFRSF21                          [IER2_T, MT1E_T, PRDM1_T]   

                                       GEM2_elements  Num_genes_GEM1  \
0            [BTG1_Fibro, DEPP1_Fibro, PTGER3_Fibro]               4   
1            [NFKBIZ_Fibro, SGK1_Fibro, TRPV1_Fibro]               4   
2  [CD74_Fibro, DLEU2_Fibro, GBP1_Fibro, GBP2_Fib...               8   
3  [BTG1_Fibro, NFKBIZ_Fibro, SGK1_Fibro, TRPV1_F...               3   
4      [ARHGEF7_Fibro, DLEU2_Fibro, LINC01355_Fibro]               3   
5       [ARHGEF7_Fibro, ELF3_Fibro, LINC02035_Fibro]               3   

   Num_genes_GEM2  GEM1vsGEM2_corr(mean)  \
0               3               0.441375   
1               3               0.425784   
2               6               0.434703   
3               4               0.444065   
4               3               0.435649   
5               3               0.447458   

   GEM1_residualvsGEM2_residual_corr(mean)  average_significance  
0                                 0.239111              0.323831  
1                                 0.265719              0.250408  
2                                 0.241581              0.299091  
3                                 0.254446              0.273682  
4                                 0.227435              0.334197  
5                                 0.207534              0.403619

In [44]:
# rank each GEM_g1 by order of name inside
grouped_df['GEM1_elements'] = grouped_df['GEM1_elements'].apply(lambda x: sorted(x))
grouped_df['GEM2_elements'] = grouped_df['GEM2_elements'].apply(lambda x: sorted(x))

In [45]:
# save the grouped_df to excel
grouped_df.to_excel(data_dir + 'CIT_results_CD8EXvsFibro_groupedLR.xlsx')